In [1]:
import numpy as np
import h5py
import glob
from pycbc import pnutils
from pycbc import catalog

In [2]:
file = glob.glob('./data_config_file_o3b//*.ini')

In [3]:
name = []
for f in file:
    name.append(f.split('-')[1][:15])

In [4]:
name.sort()

In [5]:
name

['GW191103_012549',
 'GW191105_143521',
 'GW191109_010717',
 'GW191113_071753',
 'GW191126_115259',
 'GW191127_050227',
 'GW191129_134029',
 'GW191204_110529',
 'GW191204_171526',
 'GW191215_223052',
 'GW191216_213338',
 'GW191219_163120',
 'GW191222_033537',
 'GW191230_180458',
 'GW200112_155838',
 'GW200115_042309',
 'GW200128_022011',
 'GW200129_065458',
 'GW200202_154313',
 'GW200208_130117',
 'GW200208_222617',
 'GW200209_085452',
 'GW200210_092254',
 'GW200216_220804',
 'GW200219_094415',
 'GW200220_061928',
 'GW200220_124850',
 'GW200224_222234',
 'GW200225_060421',
 'GW200302_015811',
 'GW200306_093714',
 'GW200308_173609',
 'GW200311_115853',
 'GW200316_215756',
 'GW200322_091133']

In [6]:
c = catalog.Catalog(source='gwtc-3')

def detinfo(name):
    if name == 'GW200115_042309':
        name=name+'-v2'
    else:
        name = name + '-v1'
    det = []
    for i in range(len(c.data[name]['strain'])):
        det.append(c.data[name]['strain'][i]['detector'])
    det = list(set(det))
    return det

In [11]:
import lal

def info(name):
    # read in the GWTC-3 posterior files (cosmo means cosmologically reweighted)
    h5file = glob.glob('/work/yifan.wang/4ogc/LVK/GWTC-3/*'+str(name)+'*_cosmo.h5')
    if np.size(h5file)!=1:
        print('Error!!')
    f = h5py.File(h5file[0],'r')
    # ra, dec, mass
    try:
        maxl_i = np.argmax(f['C01:IMRPhenomXPHM']['posterior_samples']['log_likelihood'][:])
        waveform = 'C01:IMRPhenomXPHM'
    except KeyError:
        maxl_i = np.argmax(f['C01:IMRPhenomXPHM:HighSpin']['posterior_samples']['log_likelihood'][:])
        waveform = 'C01:IMRPhenomXPHM:HighSpin'
    ra = f[waveform]['posterior_samples']['ra'][maxl_i]
    dec = f[waveform]['posterior_samples']['dec'][maxl_i]
    final_mass = f[waveform]['posterior_samples']['final_mass'][maxl_i]
    tref = f[waveform]['posterior_samples']['geocent_time'][maxl_i]
    m1 = f[waveform]['posterior_samples']['mass_1'][maxl_i]
    m2 = f[waveform]['posterior_samples']['mass_2'][maxl_i]
    spin1z = f[waveform]['posterior_samples']['spin_1z'][maxl_i]
    spin2z = f[waveform]['posterior_samples']['spin_2z'][maxl_i]
    
    # starting time = merger time + 10 M_f 
    toffset = 10* final_mass * lal.MTSUN_SI

    final_freq = pnutils.get_final_freq('SEOBNRv4',m1,m2,spin1z,spin2z)
    f.close()
    return ra,dec,final_mass,final_freq,toffset,tref

In [15]:
print('There are ', np.size(name), ' events')

There are  35  events


In [12]:
import os
os.remove('events.ini')
with open('events.ini', 'w') as t:
    for ii in name:
        print(ii)
        ra,dec,final_mass,final_freq,toffset,tref = info(ii)
        filedir = glob.glob('./data_config_file_o3b/*'+str(ii)+'*.ini')
        if np.size(filedir)!=1:
            print('Error!!!')
        filedir = filedir[0]
        t.write('[event-'+str(ii)+']\n')
        t.write('label='+str(ii)+'\n')
        t.write('config-files='+str(filedir)+'\n')
        t.write('\t\t\tkerr_base.ini\n')
        t.write('config-overrides =data:trigger-time:'+str(tref)+'\n')
        t.write('\t\t\tstatic_params:ra:'+str(ra)+'\n')
        t.write('\t\t\tstatic_params:dec:'+str(dec)+'\n')
        t.write('\t\t\tstatic_params:toffset:'+str(toffset)+'\n')
        if final_mass < 150 and final_mass>10:
            t.write('\t\t\tprior-final_mass:min-final_mass:10\n')
            t.write('\t\t\tprior-final_mass:max-final_mass:200\n')
        elif final_mass <= 150:
            t.write('\t\t\tprior-final_mass:min-final_mass:1\n')
            t.write('\t\t\tprior-final_mass:max-final_mass:50\n')
        else:
            t.write('\t\t\tprior-final_mass:min-final_mass:100\n')
            t.write('\t\t\tprior-final_mass:max-final_mass:500\n')

        if final_freq > 1024:
            t.write('\t\t\tdata:sample-rate:4096\n')

        #PSD time shift
        fname = ii
        if fname=='GW191109_010717':
            t.write('\t\t\tdata:psd-start-time:"H1:-100 L1:-256"\n')
            t.write('\t\t\tdata:psd-end-time:"H1:412 L1:256"\n')
        if fname == 'GW191113_071753':
            t.write('\t\t\tdata:psd-start-time:"H1:-100 L1:-256 V1:-256"\n')
            t.write('\t\t\tdata:psd-end-time:"H1:412 L1:256 V1:256"\n')
        if fname == 'GW191105_143521':
            t.write('\t\t\tdata:psd-start-time:"H1:-256 L1:-256 V1:-412"\n')
            t.write('\t\t\tdata:psd-end-time:"H1:256 L1:256 V1:100"\n')
        if fname == 'GW200316_215756':
            t.write('\t\t\tdata:psd-start-time:"H1:-256 V1:-256 L1:-30"\n')
            t.write('\t\t\tdata:psd-end-time:"H1:256 V1:256 L1:482"\n')
        
        # set the data-conditioning-low-freq for each detector combinations
        print(detinfo(ii))
        if detinfo(ii)==['L1','H1'] or detinfo(ii)==['H1','L1']:
            t.write('\t\t\tdata:data-conditioning-low-freq:"H1:0 L1:0"\n')
        if detinfo(ii)==['V1','H1'] or detinfo(ii)==['H1','V1']:
            t.write('\t\t\tdata:data-conditioning-low-freq:"H1:0 V1:0"\n')
        if detinfo(ii)==['L1','V1'] or detinfo(ii)==['V1','L1']:
            t.write('\t\t\tdata:data-conditioning-low-freq:"L1:0 V1:0"\n')
        t.write('\n')
t.close()

GW191103_012549
['H1', 'L1']
GW191105_143521
['H1', 'L1', 'V1']
GW191109_010717
['H1', 'L1']
GW191113_071753
['H1', 'L1', 'V1']
GW191126_115259
['H1', 'L1']
GW191127_050227
['H1', 'L1', 'V1']
GW191129_134029
['H1', 'L1']
GW191204_110529
['H1', 'L1']
GW191204_171526
['H1', 'L1']
GW191215_223052
['H1', 'L1', 'V1']
GW191216_213338
['H1', 'V1']
GW191219_163120
['H1', 'L1', 'V1']
GW191222_033537
['H1', 'L1']
GW191230_180458
['H1', 'L1', 'V1']
GW200112_155838
['L1', 'V1']
GW200115_042309
['H1', 'L1', 'V1']
GW200128_022011
['H1', 'L1']
GW200129_065458
['H1', 'L1', 'V1']
GW200202_154313
['H1', 'L1', 'V1']
GW200208_130117
['H1', 'L1', 'V1']
GW200208_222617
['H1', 'L1', 'V1']
GW200209_085452
['H1', 'L1', 'V1']
GW200210_092254
['H1', 'L1', 'V1']
GW200216_220804
['H1', 'L1', 'V1']
GW200219_094415
['H1', 'L1', 'V1']
GW200220_061928
['H1', 'L1', 'V1']
GW200220_124850
['H1', 'L1']
GW200224_222234
['H1', 'L1', 'V1']
GW200225_060421
['H1', 'L1']
GW200302_015811
['H1', 'V1']
GW200306_093714
['H1', 'L1']